## 3D 지도 시각화 실습    

### 패키지

In [1]:
import pandas as pd
import geopandas as gpd

c:\Users\thlee\AppData\Local\Programs\Python\Python39\lib\site-packages\geopandas\_compat.py:123: UserWarning: The Shapely GEOS version (3.10.1-CAPI-1.16.0) is incompatible with the GEOS version PyGEOS was compiled with (3.10.3-CAPI-1.16.1). Conversions between both will be slow.
  warnings.warn(


In [45]:
import pydeck as pdk
from IPython.core.display import display
from IPython.display import display
import ipywidgets as widgets

C:\Users\thlee\AppData\Local\Temp\ipykernel_21492\1946343473.py:2: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display
  from IPython.core.display import display


## 데이터 로딩 

In [2]:
geo_data = './data/gdf_gu_cctv_sl2.geojson'

# 파일을 파이썬에서 읽습니다.
import json
with open(geo_data, encoding='utf-8') as f:
    data = json.loads(f.read())

In [3]:
# pandas 패키지에서 csv를 읽는 함수명은?
df = pd.read_csv('./data/pop/2016년+3월+SKT이동통신을+이용한+성별연령별+유동인구(종로구).csv', index_col=None, header=0, 
                          names=['STD_YM', 'SI_DO_NM', 'SGNG_NM', 'ADONG_NM', 'BLOCK_CD', 'X_COORD', 'Y_COORD', 'MAN_FLOW_POP_CNT_10G', 'MAN_FLOW_POP_CNT_20G', 'MAN_FLOW_POP_CNT_30G', 'MAN_FLOW_POP_CNT_40G', 'MAN_FLOW_POP_CNT_50G', 'MAN_FLOW_POP_CNT_60GU', 'WMAN_FLOW_POP_CNT_10G', 'WMAN_FLOW_POP_CNT_20G', 'WMAN_FLOW_POP_CNT_30G', 'WMAN_FLOW_POP_CNT_40G', 'WMAN_FLOW_POP_CNT_50G', 'WMAN_FLOW_POP_CNT_60GU', 'DATA_LOAD_DT'], 
                          usecols=['SI_DO_NM', 'SGNG_NM', 'ADONG_NM', 'BLOCK_CD', 'X_COORD', 'Y_COORD', 'MAN_FLOW_POP_CNT_10G', 'MAN_FLOW_POP_CNT_20G', 'MAN_FLOW_POP_CNT_30G', 'MAN_FLOW_POP_CNT_40G', 'MAN_FLOW_POP_CNT_50G', 'MAN_FLOW_POP_CNT_60GU', 'WMAN_FLOW_POP_CNT_10G', 'WMAN_FLOW_POP_CNT_20G', 'WMAN_FLOW_POP_CNT_30G', 'WMAN_FLOW_POP_CNT_40G', 'WMAN_FLOW_POP_CNT_50G', 'WMAN_FLOW_POP_CNT_60GU'],
                          dtype={'BLOCK_CD':object, 'Y_COORD':float}, #지정안하고 로딩시 나머지 항목은 잘 인식해서...2개만 지정함
                 encoding="utf-8", 
                 delimiter=',' , #항목 구분자 '\t'
                 thousands = ',' ) #천단위 쉼표 제거   
#df.info() #행 수 및 컬럼 정보 df.shape()을 이용해도 됨
df.head() 

SI_DO_NM SGNG_NM ADONG_NM              BLOCK_CD     X_COORD    Y_COORD  \
0    서울특별시     종로구      평창동  11010560200141000001  952559.000  1956707.0   
1    서울특별시     종로구      평창동  11010560200141000001  952608.375  1956758.0   
2    서울특별시     종로구      평창동  11010560200141000001  952609.625  1956963.0   
3    서울특별시     종로구      평창동  11010560200141000001  952757.500  1957117.0   
4    서울특별시     종로구      평창동  11010560200051000001  954573.375  1957415.0   

   MAN_FLOW_POP_CNT_10G  MAN_FLOW_POP_CNT_20G  MAN_FLOW_POP_CNT_30G  \
0                  3.63                  4.67                  6.56   
1                  4.01                  5.18                  7.30   
2                  1.05                  1.76                  1.43   
3                  2.76                  3.43                  4.82   
4                  1.44                  1.50                  2.78   

   MAN_FLOW_POP_CNT_40G  MAN_FLOW_POP_CNT_50G  MAN_FLOW_POP_CNT_60GU  \
0                  8.24                  9.03                   7.77   
1                  9.16                 10.00                   8.64   
2                  1.73                  1.58                   1.55   
3                  6.07                  6.58                   5.83   
4                  3.90                  3.47                   2.96   

   WMAN_FLOW_POP_CNT_10G  WMAN_FLOW_POP_CNT_20G  WMAN_FLOW_POP_CNT_30G  \
0                   6.07                   4.44                   7.41   
1                   6.71                   4.94                   8.24   
2                   1.41                   1.79                   2.10   
3                   4.81                   3.17                   5.51   
4                   0.97                   1.75                   2.78   

   WMAN_FLOW_POP_CNT_40G  WMAN_FLOW_POP_CNT_50G  WMAN_FLOW_POP_CNT_60GU  
0                  11.23                  10.50                    8.34  
1                  12.46                  11.64                    9.25  
2                   2.53                   2.05                    2.00  
3                   8.48                   7.86                    6.29  
4                   3.75                   3.71                    3.36

In [4]:
# 총 유동인구를 만들어 봅시다
df['POP_ALL'] = df.MAN_FLOW_POP_CNT_10G + df.MAN_FLOW_POP_CNT_20G + df.MAN_FLOW_POP_CNT_30G + df.MAN_FLOW_POP_CNT_40G + df.MAN_FLOW_POP_CNT_50G + df.MAN_FLOW_POP_CNT_60GU + df.WMAN_FLOW_POP_CNT_10G + df.WMAN_FLOW_POP_CNT_20G + df.WMAN_FLOW_POP_CNT_30G + df.WMAN_FLOW_POP_CNT_40G + df.WMAN_FLOW_POP_CNT_50G + df.WMAN_FLOW_POP_CNT_60GU

In [5]:
#불필요한 항목 제거
df.drop(['SI_DO_NM', 'SGNG_NM', 'ADONG_NM', 'BLOCK_CD', 'MAN_FLOW_POP_CNT_10G', 'MAN_FLOW_POP_CNT_20G', 'MAN_FLOW_POP_CNT_30G', 'MAN_FLOW_POP_CNT_40G', 'MAN_FLOW_POP_CNT_50G', 'MAN_FLOW_POP_CNT_60GU', 'WMAN_FLOW_POP_CNT_10G', 'WMAN_FLOW_POP_CNT_20G', 'WMAN_FLOW_POP_CNT_30G', 'WMAN_FLOW_POP_CNT_40G', 'WMAN_FLOW_POP_CNT_50G', 'WMAN_FLOW_POP_CNT_60GU'], axis=1, inplace=True)
#또는 필요한 항목만 뽑아서 다른 데이터프레임으로 저장 
#df2 = df[['POP_ALL', 'X_COORD', 'Y_COORD']]

In [6]:
# 50%만 샘플링
df2 = df.sample(frac=0.5)
df2.head()

X_COORD    Y_COORD  POP_ALL
5037  954943.6250  1953355.0   140.71
3077  952467.3750  1957837.0     0.00
5625  957884.8125  1952928.0  1414.18
2289  952881.8750  1953109.0   134.36
2944  954950.0000  1954536.0    64.86

In [7]:
# 좌표 속성을 가지고 지오메트리 데이터를 생성
geom = gpd.points_from_xy(df2.X_COORD, df2.Y_COORD)
gdf_pop_5179 = gpd.GeoDataFrame(df2, geometry=geom, crs=5179) 

In [8]:
# 유동인구 좌표를 mapbox에 올리기 위해 포인트를 버퍼해서 폴리곤을 생성 
gdf_pop_5179_buf = gpd.GeoDataFrame(gdf_pop_5179.POP_ALL, geometry=gdf_pop_5179.buffer(10), crs=5179)
gdf_pop_5179_buf.head()

POP_ALL                                           geometry
5037   140.71  POLYGON ((954953.625 1953355.000, 954953.577 1...
3077     0.00  POLYGON ((952477.375 1957837.000, 952477.327 1...
5625  1414.18  POLYGON ((957894.812 1952928.000, 957894.764 1...
2289   134.36  POLYGON ((952891.875 1953109.000, 952891.827 1...
2944    64.86  POLYGON ((954960.000 1954536.000, 954959.952 1...

In [9]:
# 좌표 변환 
gdf_pop_4326_buf = gdf_pop_5179_buf.to_crs('4326')
# Geometry를 이용하여 X, Y 좌표 항목을 생성 
#gdf_pop_4326_buf["lon"] = gdf_pop_4326_buf.geometry.centroid.x
#gdf_pop_4326_buf["lat"] = gdf_pop_4326_buf.geometry.centroid.y

## 3D 시각화

### Tutorial과 데이터를 서로 바꿔서 적용해 봅시다!  
pydeck에는 "서울시 구 행정구역"를 올려보고,      
mapboxgl에는 "유동인구 좌표"를 올려 봅시다     

## pydeck   
아래 사이트의 코드를 참조하시면 구현할 수 있습니다!    
https://deckgl.readthedocs.io/en/latest/gallery/geojson_layer.html 

In [46]:
INITIAL_VIEW_STATE = pdk.ViewState(latitude=37.6, longitude=127, zoom=10, max_zoom=17, pitch=65, bearing=0)

geojson = pdk.Layer(
    "GeoJsonLayer",
    data,
    opacity=0.8,
    stroked=True,
    filled=True,
    extruded=True,
    wireframe=False,
    get_elevation="properties.size",
    get_fill_color="[properties.size * 100, properties.size * 100, 100]",
    get_line_color=[0, 0, 0],
)

r = pdk.Deck(layers=[geojson], initial_view_state=INITIAL_VIEW_STATE)
r.show() # html 저장하지 않고 바로 보고싶은 경우 사용

DeckGLWidget(carto_key=None, custom_libraries=[], google_maps_key=None, json_input='{\n  "initialViewState": {…

## mapboxgl    
https://github.com/mapbox/mapboxgl-jupyter    
mapboxgl.js를 파이썬 환경에서 쓸 수 있게 만든 패키지로, mapboxgl.js과 동일하게 Mapbox API Key인 토큰(token) 정보가 필요함      
Mapbox 웹사이트(https://www.mapbox.com/)로 이동하고 화면 하단의 "Get Started for free" 버튼을 클릭하여 회원가입    
회원가입이 된 후에는 https://account.mapbox.com/access-tokens/ 로 접속하여 "Create a token"으로 토큰(API 키)을 생성하고 복사   

In [10]:
# mapbox token 정보 읽기 
f = open('../../etc/mapbox.txt', 'r')
lines = f.readlines()
mapbox_token = lines[0]
MAPBOX_API_KEY2 = mapbox_token.replace('"','')  #문자열의 쌍따옴표 제거

In [11]:
#import mapboxgl
import os
from mapboxgl.viz import * 
from mapboxgl.utils import *

In [55]:
gdf_pop_4326_buf.POP_ALL.describe()

count    2834.000000
mean      278.726771
std       416.172757
min         0.000000
25%        26.190000
50%       126.720000
75%       350.257500
max      4933.300000
Name: POP_ALL, dtype: float64

In [27]:
##gj = gdf_pop_4326_buf.to_json()  #이걸로는 잘 안되네요...
gdf_pop_4326_buf.to_file('data/3D/pop_buf_4326.geojson', driver='GeoJSON')  

In [32]:
import geojson
with open('data/3D/pop_buf_4326.geojson') as f:
    gj = geojson.load(f)

In [43]:
from mapboxgl.utils import create_numeric_stops

# 시각화 색상 단계를 지정해줍니다.
color_stops=create_color_stops([0, 1000, 2000, 3000, 4000], colors='BuPu')  #YlOrRd, YlGnBu, 

# ChoroplethViz 를 그립니다.
viz = ChoroplethViz(data=gj,
    access_token=MAPBOX_API_KEY2,
    color_property='POP_ALL', 
    color_stops=color_stops,
    center=[126.98, 37.57],
    zoom=12)
    
# 맵을 방위와 상하 각도를 설정합니다. 
viz.bearing = 0
viz.pitch = 60
viz.style = 'mapbox://styles/mapbox/dark-v10?optimize=true' #viz.style = 'mapbox://styles/mapbox/light-v10?optimize=true'

# 각 데이터에 '인구'를 기준으로 height 값을 줍니다.
viz.height_property = 'POP_ALL' 
viz.height_stops = create_numeric_stops([0, 1000, 2000, 3000, 4000], 0, 3000)
viz.height_function_type = 'interpolate'

# render again
viz.show()

# with open('./result/mapbox.html', 'w') as f:
#     f.write(viz.create_html())

C:\Users\thlee\AppData\Roaming\Python\Python39\site-packages\IPython\core\display.py:431: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


### 맵박스에서 지원하는 배경지도 
- mapbox://styles/mapbox/streets-v11
- mapbox://styles/mapbox/outdoors-v11
- mapbox://styles/mapbox/light-v10
- mapbox://styles/mapbox/dark-v10
- mapbox://styles/mapbox/satellite-v9
- mapbox://styles/mapbox/satellite-streets-v11
- mapbox://styles/mapbox/navigation-preview-day-v4
- mapbox://styles/mapbox/navigation-preview-night-v4
- mapbox://styles/mapbox/navigation-guidance-day-v4
- mapbox://styles/mapbox/navigation-guidance-night-v4

### pydeck과 mapboxgl의 차이점    
mapboxgl은 여러 개의 레이어를 쌓지 못함 > pydeck에서는 가능   

In [ ]:
# import pandas as pd, requests, json

# 경도, 위도 속성이 포함된 DataFrame을 포인트 geoJson으로 변환하는 함수 - 경도 컬럼명은 lon, 위도 컬럼명은 lat으로 
def df_to_geojson2(df, properties, lat='lat', lon='lon'):
    # geojson 구조 정의 
    geojson = {'type':'FeatureCollection', 'features':[]}

    # 반복문을 통해 데이터프레임 파싱 
    for _, row in df.iterrows():
        feature = {'type':'Feature',
                   'properties':{},
                   'geometry':{'type':'Point',
                               'coordinates':[]}}

        # geojson의 geometry coordinates 에 경도, 위도 좌표를 적용
        feature['geometry']['coordinates'] = [row[lon],row[lat]]

        # 개별 속성정보들을 입력 
        for prop in properties:
            feature['properties'][prop] = row[prop]

        # geojson features 단위에 feature 정보를 추가     
        geojson['features'].append(feature)

    return geojson

# 이용 방법 
# cols = ['street_address', 'issue_type', 'status']
# geojson = df_to_geojson2(df, cols)     